# CORESE client: update

This notebook is intended to be used as a supplement to the _corese-query.jpynb_ notebook to test the local CORESE server. 


In [4]:
from __future__ import print_function

### Start the server if it is not already running

Run the following command from the directory where the server is downloaded

_java -jar -Dfile.encoding=UTF8 -Xmx20G corese-server-4.1.2.jar -e -lp -debug -pp profile.ttl_

or if runing on Windows change the path and run the code below.

NOTE: please notice that the server name/version in the command line should corresponds to your server executable.

In [ ]:
import os
import subprocess

corese_path = os.path.normpath('C:/Users/abobashe/Documents/MonaLIA/CORESE')
command_line = 'start /w cmd /k java -jar -Dfile.encoding=UTF8 -Xmx20G corese-server-4.1.2.jar -e -lp -debug -pp profile.ttl'

corese_server = subprocess.Popen(command_line, shell=True, cwd=corese_path)

In [5]:
import SPARQLWrapper
import json
print('SPARQLWrapper ver.', SPARQLWrapper.__version__)

from SPARQLWrapper import SPARQLWrapper, JSON, XML
from SPARQLWrapper import POST, POSTDIRECTLY

import pandas as pd
print('Pandas ver.', pd.__version__)

SPARQLWrapper ver. 1.8.5
Pandas ver. 0.23.4


In [6]:
def sparql_service_to_dataframe(service, query):
    """
    Helper function to convert SPARQL results into a Pandas DataFrame.
    
    Credit to Ted Lawless https://lawlesst.github.io/notebook/sparql-dataframe.html
    """
    sparql = SPARQLWrapper(service)
    sparql.setQuery(query)
    sparql.setReturnFormat(JSON)
    result = sparql.query()

    processed_results = json.load(result.response)
    cols = processed_results['head']['vars']

    out = []
    for row in processed_results['results']['bindings']:
        item = []
        for c in cols:
            item.append(row.get(c, {}).get('value'))
        out.append(item)

    return pd.DataFrame(out, columns=cols)


def sparql_service_update(service, update_query):
    """
    Helper function to update (DELETE DATA, INSERT DATA, DELETE/INSERT) data.
 
    """
    sparql = SPARQLWrapper(service)
    sparql.setMethod(POST)
    sparql.setRequestMethod(POSTDIRECTLY)
    sparql.setQuery(update_query)
    result = sparql.query()
    
    #SPARQLWrapper is going to throw an exception if result.response.status != 200:
                
    return 'Done'

## Update data

In [1]:
wds_Corese = 'http://localhost:8080/sparql'

In [7]:
insert = '''
PREFIX dc: <http://purl.org/dc/elements/1.1/>

INSERT DATA 
{ <http://example/book1>  dc:title  "Oliver Twist"
  <http://example/book2>  dc:title  "David Copperfield"
}

'''

delete = '''
PREFIX dc: <http://purl.org/dc/elements/1.1/>

DELETE DATA 
{ <http://example/book1>  dc:title  "Oliver Twist" }

'''

update = '''
PREFIX dc: <http://purl.org/dc/elements/1.1/>

DELETE {?x dc:title "Oliver Twist"}
INSERT {?x dc:title "Nicholas Nickleby"}
WHERE {?x dc:title "Oliver Twist" }
'''

In [8]:
sparql_service_update(wds_Corese, insert)

'Done'

In [9]:
verify_update = '''
PREFIX dc: <http://purl.org/dc/elements/1.1/>

SELECT * 
WHERE {?x dc:title ?y }
'''

In [10]:
df = sparql_service_to_dataframe(wds_Corese, verify_update)

In [12]:
pd.set_option('display.max_colwidth', -1) # if your Pandas version is < 1.0 then use -1 as second parameter, None otherwise
pd.set_option('display.precision', 3)
pd.set_option('display.max_rows', 9999)


df.head()

x                  y
0  http://example/book1  Oliver Twist     
1  http://example/book2  David Copperfield